## This notebook will be used to complete the Coursera Capstone Course

# 1. Introduction


<p> New York City comprises 5 boroughs sitting where the Hudson River meets the Atlantic Ocean. At its core is Manhattan, a densely populated borough that’s among the world’s major commercial, financial and cultural centers. Its iconic sites include skyscrapers such as the Empire State Building and sprawling Central Park. Broadway theater is staged in neon-lit Times Square. </p>
<p> The Big Apple has thousands of restaurants of all kind spread by the neighborhoods and it is a real challenge to find the best place to start a new food business anywhere in the city. </p>
<p> In this study, I will try to identify eligible spots in New York City to open a Brazilian Restaurant and my target public would be any entrepreneur who is willing to open a Brazilian restaurant in New York City. </p>

In [1]:
!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import folium # map rendering library

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2019.6.16          |           py36_1         149 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ca-certificates-2019.6.16  |       hecc5488_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

In [2]:
import pandas as pd
import numpy as np

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans


print('Libraries imported.')

Libraries imported.


In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
neighborhoods_data = newyork_data['features']
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [6]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [7]:
address = 'Forest Hills Gardens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Forest Hills Gardens are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Forest Hills Gardens are 40.71521885, -73.8426404158723.


In [8]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [9]:
# Remove Manhattan and Staten Island from the analysis
BBQ = neighborhoods['Borough'] != 'Manhattan'
bbq_data = neighborhoods[BBQ]
BBQ = bbq_data['Borough'] != 'Staten Island'
bbq_data = bbq_data[BBQ].reset_index(drop=True)

In [10]:
bbq_data['Borough'].unique()

array(['Bronx', 'Brooklyn', 'Queens'], dtype=object)

In [11]:
from folium.plugins import MarkerCluster
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

ny_cluster = MarkerCluster().add_to(map_newyork)

# add markers to map
for lat, lng, borough, neighborhood in zip(bbq_data['Latitude'], bbq_data['Longitude'], bbq_data['Borough'], bbq_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    if borough == 'Queens':
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(ny_cluster)  
    elif borough == "Bronx":
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='brown',
            fill=True,
            fill_color='#A0522D',
            fill_opacity=0.7,
            parse_html=False).add_to(ny_cluster) 
    else:
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='red',
            fill=True,
            fill_color='#FFB6C1',
            fill_opacity=0.7,
            parse_html=False).add_to(ny_cluster) 
    
map_newyork

In [12]:
CLIENT_ID = '1FK453H1EJNBMEYWHN4NZPMD0Y0LULSEXOYDXUJIVODSPRTO' # your Foursquare ID
CLIENT_SECRET = 'ABNM5MW5YRXZKXAYLFVRXQIHOYTRKSOIIV5KQSVXTVOH25TQ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1FK453H1EJNBMEYWHN4NZPMD0Y0LULSEXOYDXUJIVODSPRTO
CLIENT_SECRET:ABNM5MW5YRXZKXAYLFVRXQIHOYTRKSOIIV5KQSVXTVOH25TQ


In [13]:
bbq_data.shape

(203, 4)

In [14]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

def getNearbyVenues(names, latitudes, longitudes, radius=500, limit=50):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        #print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [15]:
bbq_data.loc[0,'Neighborhood']

'Wakefield'

In [16]:
query = 'gym'
radius=500
limit=50
venues_list=[]
# create the API request URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
          CLIENT_ID, 
          CLIENT_SECRET, 
          VERSION, 
          bbq_data.loc[2,'Latitude'], 
          bbq_data.loc[2,'Longitude'], 
          radius, 
          limit)
results = requests.get(url).json()["response"]['groups'][0]['items']
venues_list.append([(
            bbq_data.loc[2,'Neighborhood'], 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
nearby_venues.columns = ['Neighborhood', 
              'Neighborhood Latitude', 
              'Neighborhood Longitude', 
              'Venue', 
              'Venue Latitude', 
              'Venue Longitude', 
              'Venue Category']

In [17]:
nearby_venues.shape

(23, 7)

In [18]:
ny_venues = getNearbyVenues(names=bbq_data['Neighborhood'],
                                   latitudes=bbq_data['Latitude'],
                                   longitudes=bbq_data['Longitude']
                                  )

In [19]:
ny_venues.head(20)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Wakefield              40.894705              -73.847201   
1     Wakefield              40.894705              -73.847201   
2     Wakefield              40.894705              -73.847201   
3     Wakefield              40.894705              -73.847201   
4     Wakefield              40.894705              -73.847201   
5     Wakefield              40.894705              -73.847201   
6     Wakefield              40.894705              -73.847201   
7     Wakefield              40.894705              -73.847201   
8     Wakefield              40.894705              -73.847201   
9     Wakefield              40.894705              -73.847201   
10    Wakefield              40.894705              -73.847201   
11   Co-op City              40.874294              -73.829939   
12   Co-op City              40.874294              -73.829939   
13   Co-op City              40.874294              -73.829939   
14   Co-op City              40.874294              -73.829939   
15   Co-op City              40.874294              -73.829939   
16   Co-op City              40.874294              -73.829939   
17   Co-op City              40.874294              -73.829939   
18   Co-op City              40.874294              -73.829939   
19   Co-op City              40.874294              -73.829939   

                                      Venue  Venue Latitude  Venue Longitude  \
0                          Lollipops Gelato       40.894123       -73.845892   
1                                  Rite Aid       40.896649       -73.844846   
2                          Carvel Ice Cream       40.890487       -73.848568   
3   Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
4                                   Dunkin'       40.890459       -73.849089   
5                                     Shell       40.894187       -73.845862   
6                                    SUBWAY       40.890656       -73.849192   
7                               Pitman Deli       40.894149       -73.845748   
8              Baychester Avenue Food Truck       40.892293       -73.843230   
9                               Louis Pizza       40.898457       -73.848770   
10                          Koss Quick Wash       40.891147       -73.850230   
11                              Dollar Tree       40.870125       -73.828989   
12                           Capri II Pizza       40.876374       -73.829940   
13                                 Rite Aid       40.870345       -73.828302   
14                            Mattress Firm       40.872234       -73.828607   
15                           Baskin Robbins       40.870045       -73.829578   
16                                   Arby's       40.870518       -73.828657   
17                Food Universe Marketplace       40.876740       -73.828980   
18                     Townhouse Restaurant       40.876086       -73.828868   
19                     truman track n field       40.874963       -73.830847   

          Venue Category  
0           Dessert Shop  
1               Pharmacy  
2         Ice Cream Shop  
3   Caribbean Restaurant  
4             Donut Shop  
5            Gas Station  
6         Sandwich Place  
7                   Food  
8             Food Truck  
9            Pizza Place  
10            Laundromat  
11        Discount Store  
12           Pizza Place  
13              Pharmacy  
14        Mattress Store  
15        Ice Cream Shop  
16  Fast Food Restaurant  
17         Grocery Store  
18            Restaurant  
19        Baseball Field

In [20]:
brazilian_restaurants = ny_venues[ny_venues['Venue Category'] == "Brazilian Restaurant"]
brazilian_restaurants

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
2677         Astoria              40.768509              -73.915654   
4017  Rockaway Beach              40.582802              -73.822361   
4028  Rockaway Beach              40.582802              -73.822361   
4179      Ravenswood              40.761705              -73.931575   

                                 Venue  Venue Latitude  Venue Longitude  \
2677                      Favela Grill       40.767348       -73.917897   
4017                   Beach Bistro 96       40.585214       -73.817922   
4028  The Summer Shift by The MP Shift       40.585152       -73.817901   
4179            New York Pão de Queijo       40.762601       -73.925992   

            Venue Category  
2677  Brazilian Restaurant  
4017  Brazilian Restaurant  
4028  Brazilian Restaurant  
4179  Brazilian Restaurant

 Found 4 Brazilian restaurants in BBQ area. Let's plot them

In [21]:
from folium.plugins import MarkerCluster
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

ny_cluster = MarkerCluster().add_to(map_newyork)

# add markers to map
for lat, lng, name, neighborhood in zip(brazilian_restaurants['Venue Latitude'], brazilian_restaurants['Venue Longitude'], brazilian_restaurants['Venue'], brazilian_restaurants['Neighborhood']):
    label = '{}, {}'.format(name, neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(ny_cluster)
        
map_newyork

### Now let's find all restaurants in BBQ region

In [22]:
bbq_restaurants = ny_venues[ny_venues['Venue Category'].str.contains('Restaurant')]
bbq_restaurants.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
3     Wakefield              40.894705              -73.847201   
16   Co-op City              40.874294              -73.829939   
18   Co-op City              40.874294              -73.829939   
20   Co-op City              40.874294              -73.829939   
25  Eastchester              40.887556              -73.827806   

                                      Venue  Venue Latitude  Venue Longitude  \
3   Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
16                                   Arby's       40.870518       -73.828657   
18                     Townhouse Restaurant       40.876086       -73.828868   
20             Guang Hui Chinese Restaurant       40.876603       -73.829710   
25                              Fish & Ting       40.885539       -73.829151   

          Venue Category  
3   Caribbean Restaurant  
16  Fast Food Restaurant  
18            Restaurant  
20    Chinese Restaurant  
25  Caribbean Restaurant

In [23]:
bbq_restaurants.shape

(1267, 7)

In [24]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

ny_cluster = MarkerCluster().add_to(map_newyork)

# add markers to map
for lat, lng, name, category in zip(bbq_restaurants['Venue Latitude'], bbq_restaurants['Venue Longitude'], bbq_restaurants['Venue'], bbq_restaurants['Venue Category']):
    label = '{}, {}'.format(name, category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(ny_cluster)
        
map_newyork

In [25]:
bbq_restaurants['Venue Category'].unique()

array(['Caribbean Restaurant', 'Fast Food Restaurant', 'Restaurant',
       'Chinese Restaurant', 'Seafood Restaurant',
       'Latin American Restaurant', 'Mexican Restaurant',
       'Spanish Restaurant', 'Indian Restaurant', 'Italian Restaurant',
       'American Restaurant', 'Sushi Restaurant', 'French Restaurant',
       'African Restaurant', 'Paella Restaurant', 'Asian Restaurant',
       'Peruvian Restaurant', 'South American Restaurant',
       'Arepa Restaurant', 'Thai Restaurant',
       'Southern / Soul Food Restaurant', 'Comfort Food Restaurant',
       'Greek Restaurant', 'Caucasian Restaurant',
       'Middle Eastern Restaurant', 'New American Restaurant',
       'Vietnamese Restaurant', 'Shabu-Shabu Restaurant',
       'Hotpot Restaurant', 'Polish Restaurant',
       'Vegetarian / Vegan Restaurant', 'Mediterranean Restaurant',
       'Korean Restaurant', 'Eastern European Restaurant',
       'Russian Restaurant', 'Turkish Restaurant', 'Japanese Restaurant',
       'Falaf

In [26]:
south_american = bbq_restaurants[bbq_restaurants['Venue Category'].str.contains('South American Restaurant')]
latin_american = bbq_restaurants[bbq_restaurants['Venue Category'].str.contains('Latin American Restaurant')]

south_american

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
564      Clason Point              40.806551              -73.854144   
1876    Cypress Hills              40.682391              -73.876616   
2184         Downtown              40.690844              -73.983463   
2323        City Line              40.678570              -73.867976   
2510       North Side              40.714823              -73.958809   
2538       North Side              40.714823              -73.958809   
2572       South Side              40.710861              -73.958001   
2577       South Side              40.710861              -73.958001   
2780  Jackson Heights              40.751981              -73.882821   
2782  Jackson Heights              40.751981              -73.882821   
2816  Jackson Heights              40.751981              -73.882821   
2849         Elmhurst              40.744049              -73.881656   
2857         Elmhurst              40.744049              -73.881656   
2911           Corona              40.742382              -73.856825   
2960      Kew Gardens              40.705179              -73.829819   
3138        Sunnyside              40.740176              -73.926916   
3143        Sunnyside              40.740176              -73.926916   
3174        Sunnyside              40.740176              -73.926916   
3472          Bayside              40.766041              -73.774274   
4303     North Corona              40.754071              -73.857518   
4531           Utopia              40.733500              -73.796717   
5020   Middle Village              40.716415              -73.881143   

                            Venue  Venue Latitude  Venue Longitude  \
564     Maravilla's Bar and Grill       40.810829       -73.855604   
1876                      Barzola       40.681656       -73.871405   
2184                   Arepa Lady       40.691182       -73.982785   
2323                      Barzola       40.681656       -73.871405   
2510                       Tabaré       40.713069       -73.959031   
2538         Desnuda Williamsburg       40.712986       -73.958958   
2572                       Tabaré       40.713069       -73.959031   
2577         Desnuda Williamsburg       40.712986       -73.958958   
2780              La Nueva Bakery       40.750134       -73.880227   
2782            El Chivito D' Oro       40.749833       -73.882376   
2816              Pollos Mario #3       40.748220       -73.879639   
2849      Pollos a la Brasa Mario       40.747659       -73.884806   
2857              Pollos Mario #3       40.748220       -73.879639   
2911  El Palacio De Las Empanadas       40.742674       -73.854700   
2960           Tu Casa Restaurant       40.706113       -73.831586   
3138              I Love Paraguay       40.741087       -73.921490   
3143          La Pollera Colorada       40.740247       -73.923419   
3174                iloveparaguay       40.741163       -73.921479   
3472                Sabor Guarani       40.764156       -73.771272   
4303       Los Amigos Chimichurry       40.751195       -73.856925   
4531                 Tienda Vieja       40.734717       -73.794717   
5020               Rico's Chicken       40.713009       -73.877336   

                 Venue Category  
564   South American Restaurant  
1876  South American Restaurant  
2184  South American Restaurant  
2323  South American Restaurant  
2510  South American Restaurant  
2538  South American Restaurant  
2572  South American Restaurant  
2577  South American Restaurant  
2780  South American Restaurant  
2782  South American Restaurant  
2816  South American Restaurant  
2849  South American Restaurant  
2857  South American Restaurant  
2911  South American Restaurant  
2960  South American Restaurant  
3138  South American Restaurant  
3143  South American Restaurant  
3174  South American Restaurant  
3472  South American Restaurant  
4303  South American Restaurant  
4531  South American Restau

In [27]:
latin_american

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
62            Kingsbridge              40.881687              -73.902818   
99            Kingsbridge              40.881687              -73.902818   
281    University Heights              40.855727              -73.910416   
312        Morris Heights              40.847898              -73.919672   
317               Fordham              40.860997              -73.896427   
357               Fordham              40.860997              -73.896427   
416          High  Bridge              40.836623              -73.926102   
474            Mott Haven              40.806239              -73.916100   
484           Port Morris              40.801664              -73.913221   
491              Longwood              40.815099              -73.895788   
536            Morrisania              40.823592              -73.901506   
550             Soundview              40.821012              -73.865746   
617    Westchester Square              40.840619              -73.842194   
827         Schuylerville              40.826580              -73.826203   
859           Castle Hill              40.819014              -73.848027   
928             Unionport              40.829774              -73.850535   
931             Unionport              40.829774              -73.850535   
1032          Sunset Park              40.645103              -74.010316   
1039          Sunset Park              40.645103              -74.010316   
1045          Sunset Park              40.645103              -74.010316   
1364     Prospect Heights              40.676822              -73.964859   
1427         Williamsburg              40.707144              -73.958115   
1451             Bushwick              40.698116              -73.925258   
1652      Carroll Gardens              40.680540              -73.994654   
1779          Fort Greene              40.688527              -73.972906   
1875        Cypress Hills              40.682391              -73.876616   
1891        Cypress Hills              40.682391              -73.876616   
1894        Cypress Hills              40.682391              -73.876616   
1910        East New York              40.669926              -73.880699   
2133         Clinton Hill              40.693229              -73.967843   
2320            City Line              40.678570              -73.867976   
2382  Prospect Park South              40.647009              -73.962613   
2394  Prospect Park South              40.647009              -73.962613   
2558           South Side              40.710861              -73.958001   
2717              Astoria              40.768509              -73.915654   
2729             Woodside              40.746349              -73.901842   
2749             Woodside              40.746349              -73.901842   
2767             Woodside              40.746349              -73.901842   
2771             Woodside              40.746349              -73.901842   
2779      Jackson Heights              40.751981              -73.882821   
2785      Jackson Heights              40.751981              -73.882821   
2796      Jackson Heights              40.751981              -73.882821   
2815      Jackson Heights              40.751981              -73.882821   
2819      Jackson Heights              40.751981              -73.882821   
3010        Richmond Hill              40.697947              -73.831833   
3013        Richmond Hill              40.697947              -73.831833   
3157            Sunnyside              40.740176              -73.926916   
3314            Woodhaven              40.689887              -73.858110   
3343           Ozone Park              40.680708              -73.843203   
3379        College Point              40.784903              -73.843045   
3394        College Point              40.784903              -73.843045   
3451              Bayside              40.766041             

#### Given the restaurants names, it looks that some south american restaurants are brazilian ones. The same doesn't seem to happen with Latin America in the same frequence. So, I decided to cluster South American restaurants and Brazilian restaurants together and leave the other restaurants in a separate cluster

In [28]:
south_american.shape

(22, 7)

In [29]:
south_american_restaurants = south_american.append(brazilian_restaurants)
south_american_restaurants['Cluster'] = 0
south_american_restaurants

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
564      Clason Point              40.806551              -73.854144   
1876    Cypress Hills              40.682391              -73.876616   
2184         Downtown              40.690844              -73.983463   
2323        City Line              40.678570              -73.867976   
2510       North Side              40.714823              -73.958809   
2538       North Side              40.714823              -73.958809   
2572       South Side              40.710861              -73.958001   
2577       South Side              40.710861              -73.958001   
2780  Jackson Heights              40.751981              -73.882821   
2782  Jackson Heights              40.751981              -73.882821   
2816  Jackson Heights              40.751981              -73.882821   
2849         Elmhurst              40.744049              -73.881656   
2857         Elmhurst              40.744049              -73.881656   
2911           Corona              40.742382              -73.856825   
2960      Kew Gardens              40.705179              -73.829819   
3138        Sunnyside              40.740176              -73.926916   
3143        Sunnyside              40.740176              -73.926916   
3174        Sunnyside              40.740176              -73.926916   
3472          Bayside              40.766041              -73.774274   
4303     North Corona              40.754071              -73.857518   
4531           Utopia              40.733500              -73.796717   
5020   Middle Village              40.716415              -73.881143   
2677          Astoria              40.768509              -73.915654   
4017   Rockaway Beach              40.582802              -73.822361   
4028   Rockaway Beach              40.582802              -73.822361   
4179       Ravenswood              40.761705              -73.931575   

                                 Venue  Venue Latitude  Venue Longitude  \
564          Maravilla's Bar and Grill       40.810829       -73.855604   
1876                           Barzola       40.681656       -73.871405   
2184                        Arepa Lady       40.691182       -73.982785   
2323                           Barzola       40.681656       -73.871405   
2510                            Tabaré       40.713069       -73.959031   
2538              Desnuda Williamsburg       40.712986       -73.958958   
2572                            Tabaré       40.713069       -73.959031   
2577              Desnuda Williamsburg       40.712986       -73.958958   
2780                   La Nueva Bakery       40.750134       -73.880227   
2782                 El Chivito D' Oro       40.749833       -73.882376   
2816                   Pollos Mario #3       40.748220       -73.879639   
2849           Pollos a la Brasa Mario       40.747659       -73.884806   
2857                   Pollos Mario #3       40.748220       -73.879639   
2911       El Palacio De Las Empanadas       40.742674       -73.854700   
2960                Tu Casa Restaurant       40.706113       -73.831586   
3138                   I Love Paraguay       40.741087       -73.921490   
3143               La Pollera Colorada       40.740247       -73.923419   
3174                     iloveparaguay       40.741163       -73.921479   
3472                     Sabor Guarani       40.764156       -73.771272   
4303            Los Amigos Chimichurry       40.751195       -73.856925   
4531                      Tienda Vieja       40.734717       -73.794717   
5020                    Rico's Chicken       40.713009       -73.877336   
2677                      Favela Grill       40.767348       -73.917897   
4017                   Beach Bistro 96       40.585214       -73.817922   
4028  The Summer Shift by The MP Shift       40.585152       -73.817901   
4179            New York Pão de Queijo       40.762601       -73.925992   

                 Venue Category  Clust

In [30]:
for index,row in south_american_restaurants.iterrows():
    bbq_restaurants.loc[index,'Cluster'] = 0

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [31]:
bbq_restaurants['Cluster'].fillna(1,inplace=True)

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/generic.py:6130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(new_data)


In [32]:
bbq_restaurants['Cluster'].astype(int,inplace=True)
bbq_restaurants

Neighborhood  Neighborhood Latitude  \
3                     Wakefield              40.894705   
16                   Co-op City              40.874294   
18                   Co-op City              40.874294   
20                   Co-op City              40.874294   
25                  Eastchester              40.887556   
28                  Eastchester              40.887556   
31                  Eastchester              40.887556   
33                  Eastchester              40.887556   
35                  Eastchester              40.887556   
43                  Eastchester              40.887556   
62                  Kingsbridge              40.881687   
64                  Kingsbridge              40.881687   
72                  Kingsbridge              40.881687   
73                  Kingsbridge              40.881687   
77                  Kingsbridge              40.881687   
78                  Kingsbridge              40.881687   
87                  Kingsbridge              40.881687   
89                  Kingsbridge              40.881687   
99                  Kingsbridge              40.881687   
113                    Woodlawn              40.898273   
114                    Woodlawn              40.898273   
142                     Norwood              40.877224   
144                     Norwood              40.877224   
147                     Norwood              40.877224   
152                     Norwood              40.877224   
153                     Norwood              40.877224   
163                     Norwood              40.877224   
165                     Norwood              40.877224   
170              Williamsbridge              40.881039   
172                  Baychester              40.866858   
182                  Baychester              40.866858   
186                  Baychester              40.866858   
188                  Baychester              40.866858   
196              Pelham Parkway              40.857413   
197              Pelham Parkway              40.857413   
200              Pelham Parkway              40.857413   
204              Pelham Parkway              40.857413   
215              Pelham Parkway              40.857413   
220                 City Island              40.847247   
222                 City Island              40.847247   
223                 City Island              40.847247   
224                 City Island              40.847247   
225                 City Island              40.847247   
240                 City Island              40.847247   
252                Bedford Park              40.870185   
257                Bedford Park              40.870185   
258                Bedford Park              40.870185   
261                Bedford Park              40.870185   
265                Bedford Park              40.870185   
270                Bedford Park              40.870185   
273                Bedford Park              40.870185   
277                Bedford Park              40.870185   
281          University Heights              40.855727   
282          University Heights              40.855727   
292          University Heights              40.855727   
296          University Heights              40.855727   
302          University Heights              40.855727   
305              Morris Heights              40.847898   
312              Morris Heights              40.847898   
315              Morris Heights              40.847898   
317                     Fordham              40.860997   
334                     Fordham              40.860997   
337                     Fordham              40.860997   
338                     Fordham              40.860997   
345                     Fordham              40.860997   
352                     Fordham              40.860997   
357                     Fordham              40.860997   
367                East Tremont              40.842696   
377              

In [33]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

#ny_cluster = MarkerCluster().add_to(map_newyork)

# add markers to map
for lat, lng, venue, cluster in zip(bbq_restaurants['Venue Latitude'], bbq_restaurants['Venue Longitude'], bbq_restaurants['Venue'], bbq_restaurants['Cluster']):
    label = '{}'.format(venue)
    label = folium.Popup(label, parse_html=True)
    if int(cluster) == 1:
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(map_newyork)  
    else: 
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='red',
            fill=True,
            fill_color='#A0522D',
            fill_opacity=0.7,
            parse_html=False).add_to(map_newyork)     
map_newyork

## Given the map above, in blue we will find all the restaurants in BBQ area that are not Brazilian or South American. The best place to open a Brazilian restaurant would be somewere with a good number of restaurants, which means it is a restaurant area but without many red dots (South American restaurants).

## Having that said, there are many places that can be recommended to have a brazilian restaurant opened. My recommendations will be in Green 

In [34]:
address = 'Arthur Avenue, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
lat = location.latitude
long = location.longitude
print('The geograpical coordinates are {}, {}.'.format(lat, long))

The geograpical coordinates are 40.855556, -73.887568.


In [35]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

#ny_cluster = MarkerCluster().add_to(map_newyork)

# add markers to map
for lat, lng, venue, cluster in zip(bbq_restaurants['Venue Latitude'], bbq_restaurants['Venue Longitude'], bbq_restaurants['Venue'], bbq_restaurants['Cluster']):
    label = '{}'.format(venue)
    label = folium.Popup(label, parse_html=True)
    if int(cluster) == 1:
        folium.CircleMarker(
            [lat, lng],
            radius=2,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(map_newyork)  
    else: 
        folium.CircleMarker(
            [lat, lng],
            radius=3,
            popup=label,
            color='red',
            fill=True,
            fill_color='#A0522D',
            fill_opacity=0.7,
            parse_html=False).add_to(map_newyork)    
folium.Marker(
            [40.695864, -73.993760],
            popup='recommendation',
            icon=folium.Icon(color='green', icon='info-sign')).add_to(map_newyork)      
folium.Marker(
            [40.855556, -73.887568],
            popup='recommendation',
            icon=folium.Icon(color='green', icon='info-sign')).add_to(map_newyork)     

map_newyork